In [314]:
import pandas as pd
import ast
import numpy as np
from datetime import datetime
import csv
from pathlib import Path
from diversity_radio.calibration import Calibration
import json

In [387]:
version_name = ["original", "Add", "Obf"][2]  
p = ["0" ,"0.01", "0.02", "0.05", "0.1"][4]
algo= ["NRMS", "NPA", "LSTUR"][2]
k = [5, 10][1]

In [388]:
file_path = f"MIND/mind_version1/MIND_Demo_Version1/results/calibration/predictions_version_WSDM/{algo}/Greedy/preproc_{version_name}_{p}_9369Items_1000Users_behavior.tsv_2/prediction.txt"

df = pd.read_csv(file_path, sep="\t", header=None, names=["combined"])

# Split the "combined" column into "impr_index" and "pred_rank"
df[["impr_index", "pred_rank"]] = df["combined"].str.split("[", 1, expand=True)

# Strip whitespace from "impr_index" column
df["impr_index"] = df["impr_index"].str.strip()

# Remove "]" from "pred_rank" column
df["pred_rank"] = df["pred_rank"].str.replace("]", "")

# Convert "pred_rank" column to lists
df["pred_rank"] = df["pred_rank"].apply(lambda x: ast.literal_eval("[" + x + "]"))

# Create a list of dictionaries with only impr_index and pred_rank
result = df[["impr_index", "pred_rank"]].to_dict(orient="records")
# Create a list to store dictionaries
recommendation_f_list = []

# Iterate over the DataFrame rows and convert impr_index to integer
for _, row in df.iterrows():
    impr_index = int(row['impr_index'])
    pred_rank = row['pred_rank']
    recommendation_f_list.append({'impr_index': impr_index, 'pred_rank': pred_rank})

for recommendation_f in recommendation_f_list:
    print(recommendation_f)
json_file_path = "recommendations.json"
with open(json_file_path, "w") as json_file:
    json.dump(recommendation_f_list, json_file, indent=4)


/var/folders/8v/cgqpzdls33l6jdsvj3z4fdyh0000gn/T/ipykernel_24142/2001807177.py:15: FutureWarning: In a future version of pandas all arguments of StringMethods.split except for the argument 'pat' will be keyword-only.
  df[["impr_index", "pred_rank"]] = df["combined"].str.split("[", 1, expand=True)
/var/folders/8v/cgqpzdls33l6jdsvj3z4fdyh0000gn/T/ipykernel_24142/2001807177.py:21: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  df["pred_rank"] = df["pred_rank"].str.replace("]", "")


{'impr_index': 1, 'pred_rank': [7, 10, 11, 20, 23, 24, 9, 26, 12, 13, 6, 5, 25, 22, 18, 21, 28, 2, 16, 27, 19, 3, 1, 4, 15, 14, 8, 17]}
{'impr_index': 2, 'pred_rank': [39, 13, 12, 61, 42, 35, 21, 32, 36, 7, 23, 24, 30, 60, 33, 22, 20, 58, 49, 5, 57, 2, 45, 11, 1, 9, 47, 8, 51, 40, 59, 26, 37, 53, 4, 29, 14, 15, 56, 25, 19, 6, 55, 34, 44, 52, 10, 31, 46, 38, 41, 3, 18, 28, 48, 43, 54, 16, 27, 50, 17]}
{'impr_index': 3, 'pred_rank': [39, 3, 19, 25, 17, 16, 41, 8, 31, 42, 36, 23, 46, 28, 5, 51, 53, 40, 12, 4, 32, 2, 20, 49, 1, 34, 10, 13, 52, 35, 21, 11, 6, 38, 50, 48, 22, 43, 37, 33, 7, 47, 54, 26, 15, 30, 29, 45, 18, 44, 24, 9, 14, 27]}
{'impr_index': 4, 'pred_rank': [13, 8, 5, 3, 1, 2, 9, 12, 10, 7, 4, 6, 11]}
{'impr_index': 5, 'pred_rank': [7, 10, 2, 6, 4, 8, 3, 9, 5, 1]}
{'impr_index': 6, 'pred_rank': [2, 32, 6, 24, 38, 4, 14, 11, 36, 9, 18, 5, 27, 3, 25, 31, 21, 30, 26, 15, 19, 8, 37, 13, 7, 35, 1, 12, 29, 20, 17, 33, 23, 22, 16, 10, 28, 34]}
{'impr_index': 7, 'pred_rank': [34, 4, 3

In [389]:
def read_behavior_file(file):
    behavior_file = open(Path(file))
    behaviors_csv = csv.reader(behavior_file, delimiter="\t")
    behaviors = []
    for a in behaviors_csv:
        impression_index = int(a[0])  # Ensure impr_index is read as string
        userid = a[1]
        date = datetime.strptime(a[2], "%m/%d/%Y %I:%M:%S %p")
        history = a[3].split(" ")
        items = a[4].strip().split(" ")
        items_without_click = [item.split("-")[0] for item in items]
        behaviors.append({'impr_index': impression_index, "userid": userid, 'date': date, 'history': history, 'items': items, 'items_without_click': items_without_click})
    return behaviors

def read_files(article_f="data/articles.json", recommendation_f="data/recommendations.json", behavior_f="data/behaviors.tsv"):
    articles = pd.read_json(article_f)
    recommendations = pd.read_json(recommendation_f)
    behavior_file = read_behavior_file(behavior_f)
    return articles, recommendations, behavior_file
behavior_f_path = "MIND/mind_version1/MIND_Demo_Version1/valid/behaviors.tsv"
behavior_file = read_behavior_file(behavior_f_path)



articles = pd.read_csv(
    "MIND/mind_version1/MIND_Demo_Version1/valid/news.tsv", 
    sep="\t",
    names=["itemId","category","subcategory","title","abstract","url","title_entities","abstract_entities"])
articles.head(2)


itemId   category      subcategory  \
0   N3112  lifestyle  lifestyleroyals   
1  N10399       news        newsworld   

                                               title  \
0  The Brands Queen Elizabeth, Prince Charles, an...   
1  The Cost of Trump's Aid Freeze in the Trenches...   

                                            abstract  \
0  Shop the notebooks, jackets, and more that the...   
1  Lt. Ivan Molchanets peeked over a parapet of s...   

                                                 url  \
0  https://www.msn.com/en-us/lifestyle/lifestyler...   
1  https://www.msn.com/en-us/news/world/the-cost-...   

                                      title_entities  \
0  [{"Label": "Prince Philip, Duke of Edinburgh",...   
1                                                 []   

                                   abstract_entities  
0                                                 []  
1  [{"Label": "Ukraine", "Type": "G", "WikidataId...

In [390]:
# Create a dictionary to store all item IDs with their corresponding categories
all_item_categories = {}
for _, article in articles.iterrows():
    item_id = article['itemId']  # 
    category = article['category']  # 
    all_item_categories[item_id] = category


In [391]:
config = {
    'language': 'english'  
}
calibration_handler = Calibration(config)
calibration_scores_kl = []
calibration_scores_js = []


for user_behavior in behavior_file:
    impr_index_behavior = user_behavior['impr_index']
    impr_index_behavior_str = str(impr_index_behavior)
    impr_index_found = any(int(rec['impr_index']) == impr_index_behavior for rec in recommendation_f_list)
    if impr_index_found:
        # Find the recommendation entry corresponding to the current user behavior
        rec_entry = next((rec for rec in recommendation_f_list if int(rec['impr_index']) == impr_index_behavior), None)
        if rec_entry:
            pred_rank = rec_entry['pred_rank']
            item_ids = [item.split("-")[0] for item in user_behavior['items']]  # Get the item IDs and remove the suffix
            
            # Keep only the top k items based on pred_rank
            top_k_indices = sorted(range(len(pred_rank)), key=lambda i: pred_rank[i])[:k]
            pred_rank = [pred_rank[i] for i in top_k_indices]
            item_ids = [item_ids[i].split("-")[0] for i in top_k_indices]  # Remove the suffix after keeping top k items
            
            # Map item IDs to their positions based on pred_rank
            rec_list = [{'impr_index': impr_index_behavior, 'item_id': item_id, 'pred_rank': pred} for item_id, pred in zip(item_ids, pred_rank)]
            print(rec_list)

            # Append the recommendation_f_list for this behavior to the respective lists
            recommendation_f_list.extend(rec_list)
            
            user_item_ids = [item.split("-")[0] for item in user_behavior['items']][:k]  # Extract the first 3 items
            
            user_behavior_data = {'impr_index': user_behavior['impr_index'], 'items': user_item_ids}
            print("User Behavior Data:")
            print(user_behavior_data)
            
          
            all_item_ids = item_ids + user_item_ids

            all_item_categories_for_behavior = {item_id: all_item_categories[item_id] if item_id in all_item_categories else None for item_id in user_item_ids}
            all_item_categories_for_rec = {item_id: all_item_categories[item_id] if item_id in all_item_categories else None for item_id in all_item_ids}
            print("Categories:", all_item_categories_for_behavior)
            
            # Calculate calibration using user_behavior, user_item_ids, and all_item_categories_for_behavior
            user_calibration_score = calibration_handler.calculate_user_level(user_item_ids, item_ids, all_item_categories_for_rec)
            
            # Append the calibration score for this behavior to the respective lists
            calibration_scores_kl.append(user_calibration_score[0])  # Assuming KL divergence is the first element
            calibration_scores_js.append(user_calibration_score[1])  # Assuming JS divergence is the second element

# Calculate the mean calibration score for each metric
mean_calibration_score_kl = np.mean(calibration_scores_kl)
mean_calibration_score_js = np.mean(calibration_scores_js)

print(f"Mean Calibration score (KL): {mean_calibration_score_kl}")
print(f"Mean Calibration score (JS): {mean_calibration_score_js}")


[{'impr_index': 1, 'item_id': 'N27423', 'pred_rank': 1}, {'impr_index': 1, 'item_id': 'N14623', 'pred_rank': 2}, {'impr_index': 1, 'item_id': 'N28510', 'pred_rank': 3}, {'impr_index': 1, 'item_id': 'N21645', 'pred_rank': 4}, {'impr_index': 1, 'item_id': 'N23829', 'pred_rank': 5}, {'impr_index': 1, 'item_id': 'N28138', 'pred_rank': 6}, {'impr_index': 1, 'item_id': 'N23699', 'pred_rank': 7}, {'impr_index': 1, 'item_id': 'N9181', 'pred_rank': 8}, {'impr_index': 1, 'item_id': 'N6849', 'pred_rank': 9}, {'impr_index': 1, 'item_id': 'N21291', 'pred_rank': 10}]
User Behavior Data:
{'impr_index': 1, 'items': ['N23699', 'N21291', 'N1901', 'N27292', 'N17443', 'N18282', 'N6849', 'N13690', 'N12794', 'N8620']}
Categories: {'N23699': 'news', 'N21291': 'news', 'N1901': 'tv', 'N27292': 'news', 'N17443': 'entertainment', 'N18282': 'lifestyle', 'N6849': 'movies', 'N13690': 'movies', 'N12794': 'sports', 'N8620': 'news'}
{'news': 0.4, 'tv': 0.1, 'entertainment': 0.1, 'lifestyle': 0.1, 'movies': 0.2, 'sport

In [392]:
## Save the data
file_path = f"MIND/mind_version1/MIND_Demo_Version1/results/calibration/predictions_version_WSDM/{algo}/Greedy/calibration_scores_{k}_{version_name}_{p}.csv"

with open(file_path, 'w', newline='') as csvfile:
    fieldnames = ['impr_index', 'kl_divergence', 'js_divergence']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)

    writer.writeheader()
    for i in range(len(calibration_scores_kl)):
        writer.writerow({'impr_index': i+1, 'kl_divergence': calibration_scores_kl[i], 'js_divergence': calibration_scores_js[i]})


## Gini index and Coverage

In [393]:
import csv
from collections import Counter

def calculate_coverage_and_gini_index(behavior_file, recommendation_f_list, k=k):
    if not behavior_file or not recommendation_f_list:
        raise ValueError("Input data is empty")


    recommended_items = set()
    gini_index_list = []
    total_users = len(behavior_file)

    # Loop over behavior data
    for user_behavior in behavior_file:
        # Collect all unique items from user behavior
        all_items = set()
        item_ids = [item.split("-")[0] for item in user_behavior.get('items', [])]
        all_items.update(item_ids)

        # Calculate the total number of unique items
        total_items = len(all_items)

        impr_index_behavior = user_behavior.get('impr_index')
        if impr_index_behavior is None:
            continue  # Skip if impr_index is missing

        rec_entry = next((rec for rec in recommendation_f_list if int(rec.get('impr_index', -1)) == impr_index_behavior), None)
        if rec_entry:
            pred_rank = rec_entry.get('pred_rank', [])
            item_ids = [item.split("-")[0] for item in user_behavior.get('items', [])]

            # Keep only the top k items based on pred_rank
            top_k_indices = sorted(range(len(pred_rank)), key=lambda i: pred_rank[i])[:k]
            pred_rank = [pred_rank[i] for i in top_k_indices]
            item_ids = [item_ids[i] for i in top_k_indices]

            pred_rank_items = [item_ids[i] for i in range(len(pred_rank))]

            # Add recommended items to the set
            recommended_items.update(pred_rank_items)
            # print (recommended_items)

            # Calculate Gini index
            n_recommended_items = len(pred_rank_items)
            sorted_item_counts = sorted(Counter(pred_rank_items).values())
          
            coverage = len(recommended_items)

            gini_index = sum([(2 * (j + (total_items - n_recommended_items) + 1) - total_items - 1) * (cs / total_users) for j, cs in enumerate(sorted_item_counts)])
            # print (gi)
            gini_index = 1 - (gini_index / (total_users * k))
            gini_index_list.append(gini_index)

    return coverage, gini_index_list

# Call the function to calculate coverage and Gini index
coverage, gini_index_list = calculate_coverage_and_gini_index(behavior_file, recommendation_f_list, k=k)

# Save the data
file_path = f"MIND/mind_version1/MIND_Demo_Version1/results/calibration/predictions_version_WSDM/calibration_scores_{algo}.csv"

# Open the file with the modified file path in append mode
with open(file_path, 'a', newline='') as csvfile:
    fieldnames = ['k', 'version_name', 'p', 'algo', 'impr_index', 'kl_divergence', 'js_divergence', 'coverage', 'gini_index']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)

    # If the file is empty, write the header
    if csvfile.tell() == 0:
        writer.writeheader()

    # Write the rows
    for i in range(len(calibration_scores_kl)):
        writer.writerow({
            'k': k,
            'version_name': version_name,
            'p': p,
            'algo': algo,
            'impr_index': i+1, 
            'kl_divergence': calibration_scores_kl[i], 
            'js_divergence': calibration_scores_js[i],
            'coverage': coverage,  
            'gini_index': gini_index_list[i] if i < len(gini_index_list) else None  
        })

# Print the results
print(f"Total Coverage: {coverage}")
print(f"Mean Gini Index: {sum(gini_index_list) / len(gini_index_list)}" if gini_index_list else "No Gini Index data available")


Total Coverage: 1371
Mean Gini Index: 0.9999994945158341
